In [1]:
import numpy as np
import pandas as pd
import plotly.express as px


In [2]:
CONFIG = {
    'TRAIN_PATH': '/kaggle/input/datathon-entel-2022-reto2/train.csv',
    'TEST_PATH': '/kaggle/input/datathon-entel-2022-reto2/test.csv',
    'SAMPLE_SUBMISSION': '/kaggle/input/datathon-entel-2022-reto2/test_sample.csv'
}

In [3]:
df_train = pd.read_csv(CONFIG['TRAIN_PATH'])
df_test = pd.read_csv(CONFIG['TEST_PATH'])
df_sub = pd.read_csv(CONFIG['SAMPLE_SUBMISSION'])

In [4]:
df_train.head()

Z_MARCA  \
0  f223faa96f22916294922b171a2696d868fd1f9129302e...   
1  5132f94c2aebce767bd61d9e8f0d4f681d0809ca90cd2c...   
2  f223faa96f22916294922b171a2696d868fd1f9129302e...   
3  285075a02b2679248a6b4636c3328bd3097626607c3e43...   
4  df853f864c74fa85acd3a25cd0afed68f1f1d0ab249e17...   

                                              Z_GAMA  \
0  de88c121a82a06352bf1aaceba20578356408a334ba046...   
1  76df0c6db32d4e04e0ef6a3a6a1e1686677e34308d9435...   
2  de88c121a82a06352bf1aaceba20578356408a334ba046...   
3  8563abec343968034b0624650aed7254081e9e39e6b32e...   
4  8563abec343968034b0624650aed7254081e9e39e6b32e...   

                                            Z_MODELO  \
0  f0465138ce3c092d78c1e33657fe604564d40cdc8cb196...   
1  85ac1d5351fa6c551dcaf4e9440939949f59fd6986c5ee...   
2  ab82a1d82b6fbd27ffe90900dffa4e8018745ef082fdf2...   
3  3f7d19feb71e55fc12b796a4cda0fbcec00511a039e758...   
4  dbd49c8cda7f4bbbfc2a8b337b5aa79dc8067b46ca1bf5...   

                                      Z_DEPARTAMENTO  \
0  591c0a0133cb5fcd00af7bbf046f094256901239749fb7...   
1  d6c21b948958417ca98b682a573eb8aa1084b292d32f76...   
2  d6c21b948958417ca98b682a573eb8aa1084b292d32f76...   
3  d6c21b948958417ca98b682a573eb8aa1084b292d32f76...   
4  d6c21b948958417ca98b682a573eb8aa1084b292d32f76...   

                                       Z_PUNTO_VENTA  SEMANA_01  SEMANA_02  \
0  d2c888e1a77f2eb0732555cf018c3ca71bbcb32c73778c...          0          0   
1  99af5fbe4f1ce1a2d5c05d8d50543bb993dd621f259c8e...          0          0   
2  4d9927f9d9ebe9b3742b20cf87b37b72c526f39d160289...          1          0   
3  2fc9e521d966b9a311c1d3fc70abafa98dd0f37a51c71a...          0          0   
4  729be1d813198ffecf16f8c581e474cd58ee5aa7d11cdf...          0          0   

   SEMANA_03  SEMANA_04  SEMANA_05  ...  SEMANA_41  SEMANA_42  SEMANA_43  \
0          0          0          0  ...          0          0          0   
1          0          0          0  ...          0          0          0   
2          0          0          0  ...          0          0          0   
3          0          0          0  ...          0          0          0   
4          0          0          0  ...          0          0          0   

   SEMANA_44  SEMANA_45  SEMANA_46  SEMANA_47  SEMANA_48  SEMANA_49  SEMANA_50  
0          0          0          0          0          0          0          0  
1          0          0          0          0          0          0          0  
2          0          0          0          0          0          0          0  
3          0          0          0          0          0          0          0  
4          0          0          0          0          0          0          0  

[5 rows x 55 columns]

In [5]:
px.area(df_train.iloc[: , 5:].sum())

In [6]:
px.area(df_train.iloc[: , 5:].max())

In [7]:
px.area(df_train.iloc[: , 5:].mean())

In [8]:
px.area(df_train.iloc[: , 5:].std())

In [9]:
px.line(df_train.iloc[:, 5:].T.iloc[:, :20])

### Una mirada rápida a los datos
##### Los primeros datos tienen cierta ventas al principio, pero siguen con una larga tendencia de ventas nulas, esto puede ser debido a que son nuevos o que sean antiguos modelos pasado de tiempo

# Los valores totales en general

In [10]:
px.histogram(df_train.iloc[:, 5:].stack().reset_index(drop=True))

#### el valor 0 representa casi 2 millones de valores, es decir el 84% de todos los datos

In [11]:
px.scatter(df_train.iloc[:, 5:].stack().reset_index(drop=True).value_counts(normalize=True).cumsum())

#### Como se puede observar, a partir del valor 6 la diferencia en incremento de los datos varía muy poco

In [12]:
px.scatter(df_train.iloc[:, -10:].stack().reset_index(drop=True).value_counts(normalize=True).cumsum())

#### Las últimas 10 semanas siguen la tendencia de los datos

In [13]:
(df_train.iloc[:, -10:].stack().reset_index(drop=True).to_frame().rename(columns={0: 'quantity'}).quantity > 100).to_frame().value_counts(normalize=True)

quantity
False       0.999657
True        0.000343
dtype: float64

#### Los valores que sean mayor a 100 solo represetan un 0.03% de los datos en la última semana

# ¿Qué pasaría si recortamos los datos a un máximo de 100?

In [14]:
px.histogram(df_train.iloc[:, 5:].stack().apply(lambda x: x if x < 100 else 100))

#### Al cortar los datos en 100 no representa un cambio en la distribución de los datos. Esto puede ayudar a los modelos a concentrarse a predecir datos más reales que con los outliers

In [15]:
df_train.iloc[:, 5:].stack().apply(lambda x: x if x < 100 else 100).value_counts(normalize=True)

0     0.835063
1     0.072847
2     0.030825
3     0.016158
4     0.009914
        ...   
91    0.000008
89    0.000008
83    0.000007
93    0.000005
92    0.000005
Length: 101, dtype: float64

#### Como observamos los datos distribución no ha sufrido cambios